<a href="https://colab.research.google.com/github/rmd-davis/bysykkel/blob/main/bysykkel_adventure.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
'''
TODO>

Add an apply function

Reverse order of calculating seconds

Plot longest trip first, then change it to the top 20 longest

Add places where students have to write their own code

Add test cases for each block

'''

# Bysykkel i Trondheim

Du skal være konsulent for en dag, og din første kunde er Trondheim Bysykkel (et samarbeid mellom Trondheim Kommune og Clear Channel Norway AS).

Trondheim Kommune ønsker å tilby elsykler (i stedet for vanlige sykler) på de strekningene hvor folk bruker mest tid fra A til B, men de vet ikke hvilke strekgninger det gjelder. De ønsker denne informasjonen i både tabulær format og visualisert i et kart. 

De har gitt deg et Excel ark med ~140,000 turer fra 2021, og regner med at du klarer det på noen dager. Heldigvis kan du litt Pandas, og vet at du får til dette mye raskere.

## Last inn data

In [ ]:
# Colab dependencies. Uncomment, run cell, and restart runtime before continuing.
#!pip uninstall pandas-profiling
#!pip install pandas-profiling==3.1.0 -q
#!pip install pydeck -q

In [1]:
# Import packages
import pandas as pd

# Import script for code testing
# This is only needed to test the codeblocks you write in this tutorial 
from functions.codetests import codetests

In [3]:
codetests.test1(1)

Test passed, your output matched the expected output!


In [ ]:
# Load data

df = pd.read_excel('https://github.com/rmd-davis/bysykkel/blob/main/data/bysykkel_2021.xlsx?raw=true')

In [ ]:
# Inspect data

df.head(10)

Kurs i Pandas med NoA Ignite  ...            Unnamed: 10
0                             Dato:  ...                    NaN
1                               NaN  ...                    NaN
2                               NaN  ...                    NaN
3                               NaN  ...                    NaN
4                               NaN  ...                    NaN
5                        started_at  ...  end_station_longitude
6  2021-04-07 04:21:06.812000+00:00  ...              10.414788
7  2021-04-07 05:56:15.319000+00:00  ...               10.40217
8  2021-04-07 06:28:56.205000+00:00  ...              10.391444
9  2021-04-07 06:35:53.300000+00:00  ...              10.399565

[10 rows x 11 columns]

Her må vi rydde litt...
I Excel arket ligger kolonnenavnene i rad #7, så vi må bruke 'header' parameteren. Husk at Python er null-indeksert.

https://pandas.pydata.org/docs/reference/api/pandas.read_excel.html

In [ ]:
# Load data with header parameter

df = pd.read_excel('https://github.com/rmd-davis/bysykkel/blob/main/data/bysykkel_2021.xlsx?raw=true', header=6)

In [ ]:
# Inspect data after adding header parameter. 
# The first row whould contain a trip from Station 118 to Station 108

df.head()

started_at  ... end_station_longitude
0  2021-04-07 04:21:06.812000+00:00  ...             10.414788
1  2021-04-07 05:56:15.319000+00:00  ...             10.402170
2  2021-04-07 06:28:56.205000+00:00  ...             10.391444
3  2021-04-07 06:35:53.300000+00:00  ...             10.399565
4  2021-04-07 06:38:53.048000+00:00  ...             10.398101

[5 rows x 11 columns]

## Automatic EDA (Exploratory Data Analysis)

Nå kan vi bruke Pandas Profiling for å få et raskt innblikk i datasettet vårt.

https://pypi.org/project/pandas-profiling/

In [ ]:
from pandas_profiling import ProfileReport

profile = ProfileReport(df, title='Bysykkel Trondheim', html={'style':{'full_width':True}})
#ProfileReport(df)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Data cleanup

Problemer med datasettet:

* 'started_at' og 'ended_at' er strings og ikke datetime variabler
* Mangler 'start_station_name'
* Har noen ekstra kolonner vi ikke trenger
* Duplicate rows
* Mangler 'duration' for hver tur 
* 'ended_at' mangler i 703 tilfeller

### Datoer

'started_at' og 'ended_at' er 'objects', men skal være 'datetime'
<br>https://pandas.pydata.org/docs/reference/api/pandas.to_datetime.html

In [ ]:
# Use df.info() to get basic information about the dataset. Notice the Dtype for 'started_at' and 'ended_at'.

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 137160 entries, 0 to 137159
Data columns (total 11 columns):
 #   Column                     Non-Null Count   Dtype  
---  ------                     --------------   -----  
 0   started_at                 137160 non-null  object 
 1   ended_at                   136457 non-null  object 
 2   start_station_id           137160 non-null  int64  
 3   start_station_description  136297 non-null  object 
 4   start_station_latitude     137160 non-null  float64
 5   start_station_longitude    137160 non-null  float64
 6   end_station_id             137160 non-null  int64  
 7   end_station_name           137160 non-null  object 
 8   end_station_description    136917 non-null  object 
 9   end_station_latitude       137160 non-null  float64
 10  end_station_longitude      137160 non-null  float64
dtypes: float64(4), int64(2), object(5)
memory usage: 11.5+ MB


In [ ]:
# Convert 'started_at' and 'ended_at' to datetime variables

df['started_at'] = pd.to_datetime(df['started_at'])
df['ended_at'] = pd.to_datetime(df['ended_at'])

In [ ]:
# Use df.info() again, and now notice the Dtype for 'started_at' and 'ended_at'

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 137160 entries, 0 to 137159
Data columns (total 11 columns):
 #   Column                     Non-Null Count   Dtype              
---  ------                     --------------   -----              
 0   started_at                 137160 non-null  datetime64[ns, UTC]
 1   ended_at                   136457 non-null  datetime64[ns, UTC]
 2   start_station_id           137160 non-null  int64              
 3   start_station_description  136297 non-null  object             
 4   start_station_latitude     137160 non-null  float64            
 5   start_station_longitude    137160 non-null  float64            
 6   end_station_id             137160 non-null  int64              
 7   end_station_name           137160 non-null  object             
 8   end_station_description    136917 non-null  object             
 9   end_station_latitude       137160 non-null  float64            
 10  end_station_longitude      137160 non-null  float64     

### Missing data
Legg til 'start_station_name' basert på 'start_station_id', fra Excel arket som ligger i <em>'data/start_station_id.xlsx'</em>.
<br>Her kan vi bruke df.merge( ) 
<br>https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.merge.html 

In [ ]:
# Load station names Excel file into a dataframe

station_names = pd.read_excel('https://github.com/rmd-davis/bysykkel/blob/main/data/start_station_id.xlsx?raw=true')

In [ ]:
# Inspect station_names dataframe
station_names

start_station_id start_station_name
0                118         Abels gate
1                 66         Verftsbrua
2                 51            Skansen
3                108      Bassengbakken
4                 21          Bakke bru
..               ...                ...
64              2303              Tempe
65              2302  Holtermanns veg 1
66               128   Lillegårdsbakken
67              2324       SLUPPEN TEST
68              2325   Sammen for havet

[69 rows x 2 columns]

In [ ]:
# Create a merged dataframe using the original df and station_names
merged_frame = df.merge(station_names, on='start_station_id', how='left')

# Inspect created merged_frame. Notice that 'station_names' is added to the last column.
merged_frame.head(1)



started_at  ... start_station_name
0 2021-04-07 04:21:06.812000+00:00  ...         Abels gate

[1 rows x 12 columns]

In [ ]:
# Extract 'start_station_name' series as a column
station_names_column = merged_frame['start_station_name']

# Insert 'station_names_column' into original df in position 3 (after start_station_id)
df.insert(loc=3,column='start_station_name', value=station_names_column)

# Inspect resulting df
df.head()

started_at  ... end_station_longitude
0 2021-04-07 04:21:06.812000+00:00  ...             10.414788
1 2021-04-07 05:56:15.319000+00:00  ...             10.402170
2 2021-04-07 06:28:56.205000+00:00  ...             10.391444
3 2021-04-07 06:35:53.300000+00:00  ...             10.399565
4 2021-04-07 06:38:53.048000+00:00  ...             10.398101

[5 rows x 12 columns]

### Slett unødvendige kolonner

Slett 'start_station_description' og 'end_station_description'. 
<br>Bruk df.drop( ).
<br> https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.drop.html


In [ ]:
# Delete columns using df.drop()
df = df.drop(columns=['start_station_description','end_station_description'])

### Fjern duplicates

In [ ]:
# Find duplicated rows
df[df.duplicated(keep=False)]


started_at  ... end_station_longitude
29142 2021-05-24 06:45:44.267000+00:00  ...             10.444293
29143 2021-05-24 06:45:44.267000+00:00  ...             10.444293

[2 rows x 10 columns]

In [ ]:
# Inspect duplicate row using df.loc
df.loc[29143]

started_at                 2021-05-24 06:45:44.267000+00:00
ended_at                   2021-05-24 07:01:19.249000+00:00
start_station_id                                         19
start_station_name                   Jomfrugateallmenningen
start_station_latitude                            63.434423
start_station_longitude                           10.395468
end_station_id                                          236
end_station_name                    Lade idrettsanlegg vest
end_station_latitude                              63.445964
end_station_longitude                             10.444293
Name: 29143, dtype: object

In [ ]:
# Drop duplicate row

df = df.drop(29143, axis=0)

### Legg til en kolonne med tid
Legg til en kolonne som inneholder hvor lang tid hver tur tok i sekunder.
<br>Siden vi har 'started_at' og 'ended_at' klarer Pandas å regne ut tidsforskjellen automatisk som en timedelta.
<br>Bruk <code>df[column].dt.seconds</code> for å få sekunder som en float.

In [ ]:
%%time

# Calculate timedelta between 'ended_at' and 'started_at'
df['duration'] = df['ended_at'] - df['started_at']

# Convert column from timedelta to float of seconds
df['duration'] = df['duration'].dt.seconds

CPU times: user 8.77 ms, sys: 2.03 ms, total: 10.8 ms
Wall time: 11.7 ms


In [ ]:
%%time

df['duration_lambda'] = df.apply(lambda x: (x['ended_at'] - x['started_at']).seconds, axis=1)


CPU times: user 4.36 s, sys: 46.3 ms, total: 4.41 s
Wall time: 4.42 s


In [ ]:
%%time

duration_list = []
duration_value = 0

for row in df.index:
    duration_value = (df.loc[row]['ended_at'] - df.loc[row]['started_at']).seconds
    duration_list.append(duration_value)

df['duration_loop'] = duration_list


CPU times: user 48.3 s, sys: 136 ms, total: 48.4 s
Wall time: 49.1 s


### Fiks manglende verdier i 'ended_at'
* Finn gjennomsnittet av 'duration' for hvert segment i datasettet
* Bruk det som en lookup for hver rad som mangler 'duration'
* Bruk 'duration' + 'started_at' for å regne ut 'ended_at'

Se hvor mange unike segmenter det er

In [ ]:
# Make unique segment ids based on start station and end station
df['segment'] = df['start_station_id'].astype(str) + '_' + df['end_station_id'].astype(str)

unique_segments = df['segment'].unique()

print(f'Total number of unique segments: {len(unique_segments)}')


Total number of unique segments: 4311


In [ ]:
# Create dictionary of segment names and mean duration for each segment
segment_means = {}

# Loop over all of the unique segments and calculate the mean duration for that segment based on all trips for that segment

for segment in unique_segments:
    temp_frame = df[df['segment'] == segment]
    segment_means[segment] = temp_frame['duration'].mean()
    

In [ ]:
# Extract dataframe with missing ended_at values
# Use df.isna()

missing_endtime = df[df['ended_at'].isna()]
missing_endtime = missing_endtime[['started_at','segment']]

# Show missing_endtime dataframe
missing_endtime

started_at segment
5     2021-04-07 06:38:58.614000+00:00   21_30
72    2021-04-07 16:39:30.615000+00:00   29_28
106   2021-04-08 11:13:07.769000+00:00    6_21
140   2021-04-08 15:03:46.120000+00:00   41_43
174   2021-04-08 17:40:18.258000+00:00  19_126
...                                ...     ...
28904 2021-05-23 14:43:52.752000+00:00   41_18
28972 2021-05-23 17:03:24.613000+00:00   30_41
29006 2021-05-23 18:02:50.399000+00:00   95_51
29074 2021-05-23 21:27:38.510000+00:00   30_30
29108 2021-05-24 06:06:57.875000+00:00   51_41

[703 rows x 2 columns]

In [ ]:
# Fill in missing durations with values from segment_means dictionary

missing_endtime['duration'] = missing_endtime['segment'].apply(lambda x: segment_means[x]) 

# Create timedelta, needed for calculation of ended_at
missing_endtime['duration_dt'] = pd.to_timedelta(missing_endtime['duration'], unit='s')

# Calculate ended_at
missing_endtime['ended_at'] = missing_endtime['started_at'] + missing_endtime['duration_dt']

# Extract necessary columns, needed to fill original dataframe
missing_endtime = missing_endtime[['ended_at','duration']]

# Show updated dataframe
missing_endtime

ended_at     duration
5     2021-04-07 06:49:15.547333333+00:00   616.933333
72    2021-04-07 16:45:15.085085470+00:00   344.470085
106   2021-04-08 11:19:37.582953488+00:00   389.813953
140   2021-04-08 15:07:54.420613497+00:00   248.300613
174   2021-04-08 17:47:40.391333333+00:00   442.133333
...                                   ...          ...
28904    2021-05-23 14:53:40.580125+00:00   587.828125
28972 2021-05-23 17:11:02.411611111+00:00   457.798611
29006 2021-05-23 18:18:31.126272727+00:00   940.727273
29074 2021-05-23 21:49:53.103220339+00:00  1334.593220
29108 2021-05-24 06:17:20.566860465+00:00   622.691860

[703 rows x 2 columns]

In [ ]:
# Fill missing values in original dataframe based on values in missing_endtime dataframe
# df.fillna() will automatically match based on index to fill in 'ended_at' and 'duration' values

df = df.fillna(missing_endtime)

## Sjekk resultatet av data cleanup

In [ ]:
# Use df.describe() or df.describe().transpose()
df.describe()

start_station_id  start_station_latitude  ...  duration_lambda  duration_loop
count     137159.000000           137159.000000  ...    136456.000000  136456.000000
mean         298.681807               63.428478  ...       688.368720     688.368720
std          618.308959                0.008748  ...       810.508887     810.508887
min            1.000000               63.398407  ...        61.000000      61.000000
25%           41.000000               63.421867  ...       339.000000     339.000000
50%           76.000000               63.430403  ...       501.000000     501.000000
75%          123.000000               63.434423  ...       753.000000     753.000000
max         2325.000000               63.445964  ...     25726.000000   25726.000000

[8 rows x 9 columns]

In [ ]:
# Import packages for plotting

from matplotlib import pyplot as plt 
import seaborn as sns

In [ ]:
# Plot duration histogram

fig,ax = plt.subplots(figsize = (15,10))
fig = sns.histplot(data = df, x = 'duration')

## Plot de 20 lengste turene

In [ ]:
import pydeck as pdk

In [ ]:
df_map_data = df.sort_values(by='duration', na_position='first').tail(20)
df_map_data

started_at  ...   segment
137159 2021-11-30 16:37:48.976000+00:00  ...    89_293
137158 2021-11-30 16:37:47.976000+00:00  ...     29_89
137157 2021-11-30 16:37:46.976000+00:00  ...    133_29
137156 2021-11-30 16:37:45.976000+00:00  ...  1878_133
137155 2021-11-30 16:37:44.976000+00:00  ...   41_1878
137154 2021-11-30 16:37:43.976000+00:00  ...     45_41
137153 2021-11-30 16:37:42.976000+00:00  ...     55_45
137152 2021-11-30 16:37:41.976000+00:00  ...   2302_55
137151 2021-11-30 16:37:40.976000+00:00  ...  293_2302
137150 2021-11-30 16:37:39.976000+00:00  ...     25_21
137149 2021-11-30 16:37:38.976000+00:00  ...     31_16
137148 2021-11-30 16:37:37.976000+00:00  ...     52_31
137147 2021-11-30 16:37:36.976000+00:00  ...    126_14
137146 2021-11-30 16:37:35.976000+00:00  ...   109_126
137145 2021-11-30 16:37:34.976000+00:00  ...    28_109
137144 2021-11-30 16:37:33.976000+00:00  ...     74_28
137143 2021-11-30 16:37:32.976000+00:00  ...     14_74
137142 2021-11-30 16:37:31.976000+00:00  ...     43_51
137141 2021-11-30 16:37:30.976000+00:00  ...     76_43
137140 2021-11-30 16:37:29.976000+00:00  ...   2258_76

[20 rows x 14 columns]

In [ ]:
df_map_data['start_coord'] = df_map_data.apply(lambda x: [x['start_station_longitude'],x['start_station_latitude']],axis=1)
df_map_data['end_coord'] = df_map_data.apply(lambda x: [x['end_station_longitude'],x['end_station_latitude']], axis=1)

In [ ]:
layer = pdk.Layer("LineLayer", df_map_data, get_source_position="start_coord",get_target_position="end_coord", get_color = [255,0,0], get_width = 3)
init_view_state = pdk.ViewState(longitude=10.3985, latitude=63.4256, zoom=12)
r = pdk.Deck(layers=layer, initial_view_state=init_view_state, map_style='light')
r.to_html();

<IPython.core.display.Javascript object>

# Andre Pandas funskjoner som er nyttige

https://pandas.pydata.org/docs/

Les gjerne Pandas dokumentasjonen, men raskeste måte å løse et problem er vanligvis via Google og StackOverflow. Når du har et spørsmål er det veldig sannsynlig at noen andre allerede har spurt det på StackOverflow.

Det finnes MASSE artikler med 'Top n Pandas Functions'. Her er et lite utvalg av de vi har hatt nytte av i prosjekter.


Husk at mange operasjoner som gjøres på en hel DataFrame kan også gjøres på en kolonne som en Series:

```
df.method() # Accesses entire Pandas DataFrame
df['column_name'].method() # Accesses only the column as a Pandas Series
```



---



- style (precision, conditional formatting, etc)
- pd.set_option() - https://pandas.pydata.org/docs/user_guide/options.html?highlight=options%20display
- df.nlargest og df.nsmallest - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.nlargest.html?highlight=nlargest#pandas.DataFrame.nlargest
- df.idxmax() og df.idxmin() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.idxmax.html?highlight=idxmax#pandas.DataFrame.idxmax
- df.count() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.count.html?highlight=count#pandas.DataFrame.count
- df.value_counts(dropna = False) - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.value_counts.html?highlight=value_counts#pandas.DataFrame.value_counts
- df.at_time og df.between_time - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.at_time.html?highlight=at_time
- df.replace() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.replace.html?highlight=replace#pandas.DataFrame.replace
- df.fillna() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.fillna.html?highlight=fillna#pandas.DataFrame.fillna
- df.groupby() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.groupby.html?highlight=groupby#pandas.DataFrame.groupby
- df.query() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.query.html?highlight=query#pandas.DataFrame.query
- df.where() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.where.html?highlight=where#pandas.DataFrame.where
- df['column_name'].isin() - https://pandas.pydata.org/docs/reference/api/pandas.Series.isin.html?highlight=isin#pandas.Series.isin
- df['column_name'].unique() - https://pandas.pydata.org/docs/reference/api/pandas.Series.unique.html?highlight=unique#pandas.Series.unique
- df['column_name'].nunique() - https://pandas.pydata.org/docs/reference/api/pandas.Series.nunique.html?highlight=nunique#pandas.Series.nunique
- df['column_name'].cumsum() - https://pandas.pydata.org/docs/reference/api/pandas.Series.cumsum.html?highlight=cumsum#pandas.Series.cumsum
- df['column_name'].pct_change() - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.pct_change.html?highlight=pct%20change#pandas.DataFrame.pct_change
- df['column_name'].shift() - https://pandas.pydata.org/docs/reference/api/pandas.Series.shift.html?highlight=shift#pandas.Series.shift
- Windowing operations - https://pandas.pydata.org/docs/user_guide/window.html#window-expanding


- df.pipe - https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.pipe.html?highlight=pipe#pandas.DataFrame.pipe 
- Bruk av .pkl formatet for å komprimere CSV filer - https://pandas.pydata.org/docs/reference/api/pandas.read_pickle.html 
- Tips til håndtering av mye data - https://pandas.pydata.org/docs/user_guide/scale.html
- Pandas Cookbook - https://pandas.pydata.org/docs/user_guide/cookbook.html
- Built-in plotting - https://pandas.pydata.org/docs/user_guide/visualization.html




